In [222]:
import pandas as pd # need to install additional python libraries too, will be prompted
import numpy as np
from sklearn.model_selection import train_test_split


In [223]:
%pip install imbalanced-learn

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip available: 22.3 -> 23.3.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [224]:
#no truncated tables
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

In [225]:
df = pd.read_parquet("./data/catB_train.parquet")

In [226]:
df.shape

(17992, 304)

In [227]:
df["f_purchase_lh"] = df["f_purchase_lh"].fillna(0)

In [228]:
#Getting some statistics of the data..

# Identify columns with string (object) data type
string_columns = df.select_dtypes(include='object').columns
non_categorical_columns = []
# Display information for each column
for col in df.columns:
    unique_values = df[col].nunique()
    unique_values_list = df[col].unique() if unique_values < 10 else None


    # if unique_values > 6:
    #   non_categorical_columns.append[col]
    if unique_values_list is not None:
        print(f"Column: {col} | Data Type: {df[col].dtype} | Unique Values: {unique_values}")
        print(f"    Unique Values: {unique_values_list}")
        for value in unique_values_list:
            count = df[col].value_counts().get(value, 0)
            percentage = count / len(df) * 100
            print(f"        {value}: {percentage:.2f}% (Count: {count})")
    # else:
    #     print(f"Column: {col} | Data Type: {df[col].dtype} | Unique Values: {unique_values}")
    #     print(f"    Unique Values: {unique_values}")

print(non_categorical_columns)

Column: race_desc | Data Type: object | Unique Values: 4
    Unique Values: ['Chinese' 'Others' 'Indian' None 'Malay']
        Chinese: 58.47% (Count: 10520)
        Others: 9.44% (Count: 1699)
        Indian: 4.72% (Count: 849)
        None: 0.00% (Count: 0)
        Malay: 5.16% (Count: 928)
Column: clttype | Data Type: object | Unique Values: 3
    Unique Values: ['P' 'G' 'C']
        P: 81.46% (Count: 14657)
        G: 18.40% (Count: 3311)
        C: 0.13% (Count: 24)
Column: stat_flag | Data Type: object | Unique Values: 3
    Unique Values: ['ACTIVE' 'LAPSED' 'MATURED']
        ACTIVE: 95.63% (Count: 17205)
        LAPSED: 4.31% (Count: 775)
        MATURED: 0.07% (Count: 12)
Column: cltsex_fix | Data Type: object | Unique Values: 2
    Unique Values: ['Female' 'Male' None]
        Female: 45.55% (Count: 8196)
        Male: 54.32% (Count: 9773)
        None: 0.00% (Count: 0)
Column: flg_substandard | Data Type: float64 | Unique Values: 2
    Unique Values: [ 0. nan  1.]
        0.

In [229]:
#more simple stats on the columns....

unique_counts = df.nunique(dropna=False)

# Categorize columns based on the number of unique values
zero_unique = unique_counts[unique_counts == 0].index
one_unique = unique_counts[unique_counts == 1].index
two_unique = unique_counts[unique_counts == 2].index
three_unique = unique_counts[unique_counts == 3].index
more_than_three_unique = unique_counts[unique_counts > 3].index

# Display the results
print(f"Columns with 0 unique values: {zero_unique}")
print(f"Columns with 1 unique value: {one_unique}")
print(f"Columns with 2 unique values: {two_unique}")
print(f"Columns with 3 unique values: {three_unique}")
print(f"Columns with more than 3 unique values: {more_than_three_unique}")

Columns with 0 unique values: Index([], dtype='object')
Columns with 1 unique value: Index(['ape_gi_42e115', 'ape_ltc_1280bf', 'ape_inv_dcd836', 'ape_lh_d0adeb',
       'ape_gi_a10d1b', 'ape_gi_29d435', 'ape_gi_856320', 'ape_gi_058815',
       'ape_32c74c', 'sumins_gi_42e115', 'sumins_ltc_1280bf',
       'sumins_inv_dcd836', 'sumins_lh_d0adeb', 'sumins_grp_22decf',
       'sumins_gi_a10d1b', 'sumins_gi_29d435', 'sumins_lh_e22a6a',
       'sumins_grp_e04c3a', 'sumins_gi_856320', 'sumins_grp_94baec',
       'sumins_gi_058815', 'sumins_32c74c', 'prempaid_gi_42e115',
       'prempaid_ltc_1280bf', 'prempaid_inv_dcd836', 'prempaid_lh_d0adeb',
       'prempaid_gi_a10d1b', 'prempaid_gi_29d435', 'prempaid_gi_856320',
       'prempaid_gi_058815', 'prempaid_32c74c', 'ape_d0adeb', 'ape_gi',
       'f_hold_d0adeb', 'f_hold_gi', 'sumins_e22a6a', 'sumins_d0adeb',
       'sumins_gi', 'prempaid_d0adeb', 'prempaid_gi', 'f_ever_bought_d0adeb',
       'n_months_last_bought_d0adeb', 'f_ever_bought_ltc_1280

In [230]:
#Columns that are all nan or none values or only having a single value cannot
#help us to make any decicions.
cols_to_drop = df.columns[df.nunique(dropna=False).isin([1])]

# Drop the identified columns
df_dropped = df.drop(columns=cols_to_drop)
df = df_dropped
df.shape

(17992, 247)

In [231]:
df = df.drop("clntnum",axis=1)

In [232]:
#shwo all the column statistic that start with flg and end with ever.
# Select columns that start with 'flg' and end with 'ever'
selected_columns = df.loc[:, [col for col in df.columns if col.startswith('flg') and col.endswith('ever')]]

# List down unique values with their occurrences for each selected column
for col in selected_columns.columns:
    value_counts = df[col].value_counts(dropna=False)
    print(f"Column: {col}")
    for value, count in value_counts.items():
        print(f"    {value}: {count} occurrences")
    print()

Column: flg_affconnect_show_interest_ever
    nan: 17497 occurrences
    1.0: 495 occurrences

Column: flg_affconnect_ready_to_buy_ever
    nan: 17178 occurrences
    1.0: 814 occurrences

Column: flg_affconnect_lapse_ever
    nan: 17178 occurrences
    0.0: 805 occurrences
    1.0: 9 occurrences

Column: flg_hlthclaim_839f8a_ever
    nan: 17707 occurrences
    1.0: 285 occurrences

Column: flg_hlthclaim_14cb37_ever
    nan: 16617 occurrences
    1.0: 1375 occurrences



In [233]:
#sum up flg_hlthclaim_..._ever

# Identify columns starting with 'flg_hlthclaim'
flg_hlthclaim_columns = [col for col in df.columns if col.startswith('flg_hlthclaim')]

# Create a new column 'flg_hthclaim_sum' containing the sum of values in 'flg_hlthclaim' columns
df['flg_hthclaim_sum'] = df[flg_hlthclaim_columns].sum(axis=1)

# Remove the original 'flg_hlthclaim' columns
# df = df.drop(columns=flg_hlthclaim_columns)

In [234]:
#do operations on the above slected columns.display
# Select columns that start with 'flg' and end with 'ever'
selected_columns = df.loc[:, [col for col in df.columns if col.startswith('flg') and col.endswith('ever')]]

# Replace NaN based on the specified conditions
for col in selected_columns.columns:
    least_occurred_value = selected_columns[col].value_counts().idxmin()
    df[col] = df[col].fillna(abs(1-int(least_occurred_value)))


In [235]:
#do operations that on flg columns what does not end with ever
# Select columns that start with 'flg_' and do not end with 'ever'
selected_columns = df.loc[:, [col for col in df.columns if col.startswith('flg_') and not col.endswith('ever')]]

# Replace NaN values with the majority value in each selected column
for col in selected_columns.columns:
    majority_value = selected_columns[col].mode().iloc[0]  # mode() returns a Series, so we take the first value
    df[col] = df[col].fillna(majority_value)

#or also can replace with the distributoin...
# for col in selected_columns.columns:
#     df[col].fillna(pd.Series(np.random.choice(df[col].dropna(), size=len(df[col])), index=df.index), inplace=True)



In [236]:
#for is_consent and is_valid
# Identify columns that start with 'is_consent' and 'is_valid'
selected_columns = df.loc[:, df.columns[df.columns.str.startswith('is_consent') | df.columns.str.startswith('is_valid')]]

# # Replace NaN values with 0 in the selected columns
df[selected_columns.columns] = df[selected_columns.columns].fillna(0)

#Can replace with the distribution too.
# for col in selected_columns:
#   df[col].fillna(pd.Series(np.random.choice(df[col].dropna(), size=len(df[col])), index=df.index), inplace=True)



In [237]:
#comb through all the remaining group data.
# Drop columns with only one valid value
# df.replace(['None', 'none', 'NONE'], np.nan, inplace=True)
valid_counts = df.count()
# columns_to_drop = valid_counts[valid_counts == 1].index
# df = df.drop(columns=columns_to_drop)

# Replace NaN values in columns with 2 to 5 valid values randomly based on the distribution
for col in df.columns:
    # if 2 <= valid_counts[col] <= 10:
    if 2 <= df[col].nunique() <= 10:
        df[col].fillna(pd.Series(np.random.choice(df[col].dropna(), size=len(df[col])), index=df.index), inplace=True)
        # unique_values = df[col].dropna().unique()
        # probabilities = df[col].value_counts(normalize=True).dropna()
        # random_values = np.random.choice(unique_values, size=df.shape[0], p=probabilities)
        # df[col] = df[col].combine_first(pd.Series(random_values, index=df.index))


In [238]:
#Add the is consent and is valid together

# Identify columns starting with 'is_consent' and 'is_valid'
is_consent_columns = [col for col in df.columns if col.startswith('is_consent')]
is_valid_columns = [col for col in df.columns if col.startswith('is_valid')]

# Create new columns 'is_consent_sum' and 'is_valid_sum' containing the sums
df['is_consent_sum'] = df[is_consent_columns].sum(axis=1)
df['is_valid_sum'] = df[is_valid_columns].sum(axis=1)
df['is_valid_consent_sum'] = df[['is_valid_sum', 'is_consent_sum']].min(axis=1)
df['is_valid_consent_multiply'] = df['is_valid_sum'] * df['is_consent_sum']


# Remove the original 'is_consent' and 'is_valid' columns
# df = df.drop(columns=is_consent_columns + is_valid_columns)


In [239]:
#add all f_ever_bought togehter

# Identify columns starting with 'f_ever_bought'
f_ever_bought_columns = [col for col in df.columns if col.startswith('f_ever_bought')]

# Create a new column 'f_ever_bought_sum' containing the sum of values in 'f_ever_bought' columns
df['f_ever_bought_sum'] = df[f_ever_bought_columns].sum(axis=1)

# Remove the original 'f_ever_bought' columns
# df = df.drop(columns=f_ever_bought_columns)

In [240]:
#put all f_hold togehter
# Identify columns starting with 'f_hold'
f_hold_columns = [col for col in df.columns if col.startswith('f_hold')]

# Create a new column 'f_hold_sum' containing the sum of values in 'f_hold' columns
df['f_hold_sum'] = df[f_hold_columns].sum(axis=1)

# Remove the original 'f_hold' columns
# df = df.drop(columns=f_hold_columns)

In [241]:
#filling columns with one actual value and one nan
# Replace NaN values in 'f_ever_declined_la' with 0
df['f_ever_declined_la'] = df['f_ever_declined_la'].fillna(0)
# Replace NaN values in 'is_dependent_in_at_least_1_policy' with 1
df['is_dependent_in_at_least_1_policy'] = df['is_dependent_in_at_least_1_policy'].fillna(1)



In [242]:
#Adding client money status togehter
# Specify columns to be summed
roles_columns = ['flg_substandard', 'flg_is_borderline_standard', 'flg_is_revised_term', 'flg_is_rental_flat']

# Create a new column 'flg_poor' containing the sum of values in the specified columns
df['flg_poor'] = df[roles_columns].sum(axis=1)

# Remove the original columns
# df = df.drop(columns=roles_columns)

In [243]:
df['race_desc'].fillna('Chinese')
# df.dropna(subset = ['race_desc'], inplace = True)
# Fill NaN values in column 'A' with values sampled from its distribution
# df['race_desc'].fillna(pd.Series(np.random.choice(df['race_desc'].dropna(), size=len(df['race_desc'])), index=df.index), inplace=True)


19550    Chinese
4600     Chinese
13337     Others
15074    Chinese
19724    Chinese
14717    Chinese
6307     Chinese
4168      Indian
169      Chinese
11816    Chinese
14245    Chinese
4618     Chinese
11928     Others
11195    Chinese
6492     Chinese
10520    Chinese
18743     Others
15299     Indian
17470    Chinese
17726    Chinese
5923     Chinese
18769     Others
12938    Chinese
3310     Chinese
3165     Chinese
16323    Chinese
12842    Chinese
2781     Chinese
4417     Chinese
7319     Chinese
4816      Indian
2277     Chinese
137      Chinese
7014     Chinese
3481     Chinese
15886    Chinese
6848     Chinese
4189      Others
19853    Chinese
8332     Chinese
9742      Others
3704      Others
8029     Chinese
12034    Chinese
2748      Indian
5391     Chinese
4197     Chinese
2988     Chinese
19557    Chinese
17969     Indian
7930     Chinese
19273    Chinese
17497    Chinese
14239    Chinese
13672    Chinese
18902    Chinese
1397     Chinese
7655     Chinese
15808    Chine

In [244]:
#one hot encode race, client flag, stat flag
# # One-hot encode the categorical columns
# df_encoded = pd.get_dummies(df, columns=['race_desc', 'clttype', 'stat_flag'], prefix=['race', 'clttype', 'stat_flag'])
# df = df_encoded
# Assuming 'df' is your DataFrame
df['is_chinese'] = df['race_desc'].apply(lambda x: 1 if x == 'Chinese' else 0)

# Drop the original 'race_desc' column
df = df.drop(columns=['race_desc'])

#one hot encode the gender
# Map 'Female' to 1 and 'Male' to 0 in the 'cltsex_fix' column
df['cltsex_fix'] = df['cltsex_fix'].map({'Female': 1, 'Male': 0})


In [245]:
#dealing with ordered data
mapping = {'1': 0, '3': 1, '4': 2, '>4': 5, '2': 3, '0': 4}
df['hh_size_est'] = df['hh_size_est'].map(mapping)

# Define the custom encoding order
custom_order = {'E.BELOW30K': 0, 'D.30K-60K': 1, 'C.60K-100K': 2, 'B.100K-200K': 3, 'A.ABOVE200K': 4}

# Map the values in 'income_group' to integers based on the custom order
df['annual_income_est'] = df['annual_income_est'].map(custom_order)



In [246]:
#dealing with lapse data
# Replace None with -1 in columns starting with 'lapse'
lapse_columns = [col for col in df.columns if col.startswith('lapse')]
df[lapse_columns] = df[lapse_columns].replace({None: -1})

# Create a new column 'lapse_sum' containing the sum of values in 'lapse' columns
df['lapse_sum'] = df[lapse_columns].sum(axis=1)

# Remove the original 'lapse' columns
# df = df.drop(columns=lapse_columns)


In [247]:
# added here
convert_to_int = ["hh_20","pop_20", 'n_months_since_lapse_ltc_1280bf', 'n_months_since_lapse_grp_6fc3e6', 'n_months_since_lapse_grp_de05ae', 'n_months_since_lapse_inv_dcd836',
                  'n_months_since_lapse_grp_945b5a', 'n_months_since_lapse_grp_6a5788', 'n_months_since_lapse_ltc_43b9d5', 'n_months_since_lapse_grp_9cdedf', 'n_months_since_lapse_lh_d0adeb',
                  'n_months_since_lapse_grp_1581d7', 'n_months_since_lapse_grp_22decf', 'n_months_since_lapse_lh_507c37', 'n_months_since_lapse_lh_839f8a', 'n_months_since_lapse_inv_e9f316',
                  'n_months_since_lapse_grp_caa6ff', 'n_months_since_lapse_grp_fd3bfb', 'n_months_since_lapse_lh_e22a6a', 'n_months_since_lapse_grp_70e1dd', 'n_months_since_lapse_grp_e04c3a',
                  'n_months_since_lapse_grp_fe5fb8', 'n_months_since_lapse_grp_94baec', 'n_months_since_lapse_grp_e91421', 'n_months_since_lapse_lh_f852af', 'n_months_since_lapse_lh_947b15',
                  'n_months_since_lapse_32c74c',"affcon_visit_days","clmcon_visit_days","recency_clmcon_regis","recency_hlthclaim","hlthclaim_cnt_success",'hlthclaim_cnt_success', 'recency_hlthclaim_success',
                  'hlthclaim_cnt_unsuccess', 'recency_hlthclaim_unsuccess', 'flg_hlthclaim_839f8a_ever', 'recency_hlthclaim_839f8a', 'flg_hlthclaim_14cb37_ever', 'recency_hlthclaim_14cb37',
                  "n_months_last_bought_grp_6fc3e6","n_months_last_bought_grp_945b5a","n_months_last_bought_grp_6a5788","n_months_last_bought_ltc_43b9d5","n_months_last_bought_grp_9cdedf","n_months_last_bought_grp_1581d7",
"n_months_last_bought_grp_22decf","n_months_last_bought_lh_507c37","n_months_last_bought_lh_839f8a","n_months_last_bought_inv_e9f316","n_months_last_bought_grp_caa6ff","n_months_last_bought_grp_fd3bfb",
"n_months_last_bought_lh_e22a6a","n_months_last_bought_grp_70e1dd","n_months_last_bought_grp_e04c3a","n_months_last_bought_grp_fe5fb8","n_months_last_bought_grp_94baec",
"n_months_last_bought_grp_e91421","n_months_last_bought_lh_f852af","n_months_last_bought_lh_947b15","n_months_last_bought_32c74c"]
convert_to_float=["ape_grp_6fc3e6","ape_grp_de05ae","ape_grp_945b5a","ape_grp_6a5788","ape_ltc_43b9d5","ape_grp_9cdedf","ape_grp_1581d7","ape_grp_22decf","ape_lh_507c37",
                  "ape_lh_839f8a","ape_inv_e9f316","ape_grp_caa6ff","ape_grp_fd3bfb","ape_lh_e22a6a","ape_grp_70e1dd","ape_grp_e04c3a","ape_grp_fe5fb8","ape_grp_94baec",
                  "ape_grp_e91421","ape_lh_f852af","ape_lh_947b15","sumins_grp_6fc3e6","sumins_grp_de05ae","sumins_grp_945b5a","sumins_grp_6a5788","sumins_ltc_43b9d5",
                  "sumins_grp_9cdedf","sumins_grp_1581d7","sumins_lh_507c37","sumins_inv_e9f316","sumins_grp_caa6ff","sumins_grp_fd3bfb","sumins_grp_70e1dd","sumins_grp_e91421",
                  "sumins_lh_f852af","sumins_lh_947b15","prempaid_grp_6fc3e6","prempaid_grp_de05ae","prempaid_grp_de05ae","prempaid_grp_945b5a","prempaid_grp_6a5788",
                  "prempaid_ltc_43b9d5","prempaid_grp_9cdedf","prempaid_grp_1581d7","prempaid_grp_1581d7","prempaid_lh_507c37","prempaid_lh_839f8a","prempaid_inv_e9f316",
                  "prempaid_grp_caa6ff","prempaid_grp_fd3bfb","prempaid_lh_e22a6a","prempaid_grp_70e1dd","prempaid_grp_e04c3a","prempaid_grp_fe5fb8","prempaid_grp_94baec",
                  "prempaid_grp_e91421","prempaid_lh_f852af","prempaid_lh_947b15","ape_839f8a","ape_e22a6a","ape_c4bda5","ape_ltc","ape_507c37","sumins_839f8a","sumins_c4bda5",
                  "sumins_ltc","sumins_507c37","prempaid_839f8a","prempaid_e22a6a","prempaid_c4bda5","prempaid_ltc","prempaid_507c37","lapse_ape_grp_6fc3e6","lapse_ape_grp_945b5a",
                  "lapse_ape_grp_6a5788","lapse_ape_ltc_43b9d5","lapse_ape_grp_9cdedf","lapse_ape_grp_1581d7","lapse_ape_grp_22decf","lapse_ape_lh_507c37","lapse_ape_lh_839f8a",
                  "lapse_ape_grp_caa6ff","lapse_ape_grp_fd3bfb","lapse_ape_lh_e22a6a","lapse_ape_grp_70e1dd","lapse_ape_grp_e04c3a","lapse_ape_grp_fe5fb8","lapse_ape_grp_94baec",
                  "lapse_ape_grp_e91421","lapse_ape_lh_f852af","lapse_ape_lh_947b15", 'lapse_ape_32c74c','hlthclaim_amt', 'f_ever_bought_839f8a', 'f_ever_bought_e22a6a', 'f_ever_bought_d0adeb', 'f_ever_bought_c4bda5',
'f_ever_bought_ltc', 'f_ever_bought_507c37', 'f_ever_bought_gi', 'n_months_last_bought_839f8a', 'n_months_last_bought_e22a6a', 'n_months_last_bought_d0adeb', 'n_months_last_bought_c4bda5', 'n_months_last_bought_ltc',
                  'n_months_last_bought_507c37', 'n_months_last_bought_gi', 'f_ever_bought_ltc_1280bf', 'f_ever_bought_grp_6fc3e6', 'f_ever_bought_grp_de05ae', 'f_ever_bought_inv_dcd836', 'f_ever_bought_grp_945b5a',
                  'f_ever_bought_grp_6a5788', 'f_ever_bought_ltc_43b9d5', 'f_ever_bought_grp_9cdedf', 'f_ever_bought_lh_d0adeb', 'f_ever_bought_grp_1581d7', 'f_ever_bought_grp_22decf', 'f_ever_bought_lh_507c37',
                  'f_ever_bought_lh_839f8a', 'f_ever_bought_inv_e9f316', 'f_ever_bought_grp_caa6ff', 'f_ever_bought_grp_fd3bfb', 'f_ever_bought_lh_e22a6a', 'f_ever_bought_grp_70e1dd', 'f_ever_bought_grp_e04c3a',
                  'f_ever_bought_grp_fe5fb8', 'f_ever_bought_grp_94baec', 'f_ever_bought_grp_e91421', 'f_ever_bought_lh_f852af', 'f_ever_bought_lh_947b15', 'f_ever_bought_32c74c', 'n_months_last_bought_ltc_1280bf',
                  'n_months_last_bought_grp_6fc3e6', 'n_months_last_bought_grp_de05ae', 'n_months_last_bought_inv_dcd836', 'n_months_last_bought_grp_945b5a', 'n_months_last_bought_grp_6a5788', 'n_months_last_bought_ltc_43b9d5',
                  'n_months_last_bought_grp_9cdedf', 'n_months_last_bought_lh_d0adeb', 'n_months_last_bought_grp_1581d7', 'n_months_last_bought_grp_22decf', 'n_months_last_bought_lh_507c37', 'n_months_last_bought_lh_839f8a',
                  'n_months_last_bought_inv_e9f316', 'n_months_last_bought_grp_caa6ff', 'n_months_last_bought_grp_fd3bfb', 'n_months_last_bought_lh_e22a6a', 'n_months_last_bought_grp_70e1dd', 'n_months_last_bought_grp_e04c3a',
                  'n_months_last_bought_grp_fe5fb8', 'n_months_last_bought_grp_94baec', 'n_months_last_bought_grp_e91421', 'n_months_last_bought_lh_f852af', 'n_months_last_bought_lh_947b15', 'n_months_last_bought_32c74c', 'f_elx',
                  'f_mindef_mha', 'f_retail', 'flg_affconnect_show_interest_ever', 'flg_affconnect_ready_to_buy_ever', 'flg_affconnect_lapse_ever', 'affcon_visit_days', 'n_months_since_visit_affcon', 'clmcon_visit_days', 'recency_clmcon',
                  'recency_clmcon_regis', 'hlthclaim_amt', 'recency_hlthclaim', 'giclaim_amt', 'recency_giclaim', 'giclaim_cnt_success', 'recency_giclaim_success', 'giclaim_cnt_unsuccess', 'recency_giclaim_unsuccess']

# check the difference of sumins_lh_507c37 and sumins_507c37

fill_nan_with_mean = ["hh_size"]
fill_nan_with_mean_int = ["hh_20","pop_20"]
fill_nan_with_max_int= ["n_months_last_bought_products","recency_hlthclaim_839f8a","recency_hlthclaim_14cb37"]
fill_nan_with_majority = ["ctrycode_desc"]
# "recency_laspe",
fill_nan_with_n1 = ["recency_lapse","recency_cancel","lapse_ape_grp_6fc3e6","lapse_ape_grp_945b5a","lapse_ape_grp_6a5788","lapse_ape_ltc_43b9d5","lapse_ape_grp_9cdedf","lapse_ape_grp_22decf",
                    "lapse_ape_lh_507c37","lapse_ape_lh_839f8a","lapse_ape_grp_caa6ff","lapse_ape_grp_fd3bfb","lapse_ape_lh_e22a6a","lapse_ape_grp_70e1dd","lapse_ape_grp_e04c3a","lapse_ape_grp_fe5fb8",
                    "lapse_ape_grp_e91421","lapse_ape_lh_f852af","lapse_ape_lh_947b15", 'lapse_ape_32c74c', 'n_months_since_lapse_ltc_1280bf', 'n_months_since_lapse_grp_6fc3e6', 'n_months_since_lapse_grp_de05ae', 'n_months_since_lapse_inv_dcd836', 'n_months_since_lapse_grp_945b5a', 'n_months_since_lapse_grp_6a5788', 'n_months_since_lapse_ltc_43b9d5', 'n_months_since_lapse_grp_9cdedf', 'n_months_since_lapse_lh_d0adeb', 'n_months_since_lapse_grp_1581d7', 'n_months_since_lapse_grp_22decf', 'n_months_since_lapse_lh_507c37', 'n_months_since_lapse_lh_839f8a', 'n_months_since_lapse_inv_e9f316', 'n_months_since_lapse_grp_caa6ff', 'n_months_since_lapse_grp_fd3bfb', 'n_months_since_lapse_lh_e22a6a', 'n_months_since_lapse_grp_70e1dd', 'n_months_since_lapse_grp_e04c3a', 'n_months_since_lapse_grp_fe5fb8', 'n_months_since_lapse_grp_94baec', 'n_months_since_lapse_grp_e91421', 'n_months_since_lapse_lh_f852af', 'n_months_since_lapse_lh_947b15', 'n_months_since_lapse_32c74c', 'f_ever_bought_839f8a', 'f_ever_bought_e22a6a', 'f_ever_bought_d0adeb', 'f_ever_bought_c4bda5',
'f_ever_bought_ltc', 'f_ever_bought_507c37', 'f_ever_bought_gi', 'n_months_last_bought_839f8a', 'n_months_last_bought_e22a6a', 'n_months_last_bought_d0adeb', 'n_months_last_bought_c4bda5', 'n_months_last_bought_ltc', 'n_months_last_bought_507c37',
                    'n_months_last_bought_gi',"affcon_visit_days", 'f_ever_bought_ltc_1280bf', 'f_ever_bought_grp_6fc3e6', 'f_ever_bought_grp_de05ae', 'f_ever_bought_inv_dcd836', 'f_ever_bought_grp_945b5a',
                    'f_ever_bought_grp_6a5788', 'f_ever_bought_ltc_43b9d5', 'f_ever_bought_grp_9cdedf', 'f_ever_bought_lh_d0adeb', 'f_ever_bought_grp_1581d7', 'f_ever_bought_grp_22decf', 'f_ever_bought_lh_507c37',
                    'f_ever_bought_lh_839f8a', 'f_ever_bought_inv_e9f316', 'f_ever_bought_grp_caa6ff', 'f_ever_bought_grp_fd3bfb', 'f_ever_bought_lh_e22a6a', 'f_ever_bought_grp_70e1dd', 'f_ever_bought_grp_e04c3a',
                    'f_ever_bought_grp_fe5fb8', 'f_ever_bought_grp_94baec', 'f_ever_bought_grp_e91421', 'f_ever_bought_lh_f852af', 'f_ever_bought_lh_947b15', 'f_ever_bought_32c74c', 'n_months_last_bought_ltc_1280bf',
                    'n_months_last_bought_grp_6fc3e6', 'n_months_last_bought_grp_de05ae', 'n_months_last_bought_inv_dcd836', 'n_months_last_bought_grp_945b5a', 'n_months_last_bought_grp_6a5788', 'n_months_last_bought_ltc_43b9d5',
                    'n_months_last_bought_grp_9cdedf', 'n_months_last_bought_lh_d0adeb', 'n_months_last_bought_grp_1581d7', 'n_months_last_bought_grp_22decf', 'n_months_last_bought_lh_507c37', 'n_months_last_bought_lh_839f8a',
                    'n_months_last_bought_inv_e9f316', 'n_months_last_bought_grp_caa6ff', 'n_months_last_bought_grp_fd3bfb', 'n_months_last_bought_lh_e22a6a', 'n_months_last_bought_grp_70e1dd', 'n_months_last_bought_grp_e04c3a',
                    'n_months_last_bought_grp_fe5fb8', 'n_months_last_bought_grp_94baec', 'n_months_last_bought_grp_e91421', 'n_months_last_bought_lh_f852af', 'n_months_last_bought_lh_947b15', 'n_months_last_bought_32c74c', 'f_elx',
                    'f_mindef_mha', 'f_retail', 'flg_affconnect_show_interest_ever', 'flg_affconnect_ready_to_buy_ever', 'flg_affconnect_lapse_ever', 'affcon_visit_days', 'n_months_since_visit_affcon', 'clmcon_visit_days', 'recency_clmcon',
                    "recency_hlthclaim",'recency_clmcon_regis', 'hlthclaim_amt', 'recency_hlthclaim', 'hlthclaim_cnt_success', 'recency_hlthclaim_success', 'hlthclaim_cnt_unsuccess', 'recency_hlthclaim_unsuccess',"n_months_last_bought_grp_6fc3e6","n_months_last_bought_grp_945b5a","n_months_last_bought_grp_6a5788","n_months_last_bought_ltc_43b9d5","n_months_last_bought_grp_9cdedf","n_months_last_bought_grp_1581d7",
"n_months_last_bought_grp_22decf","n_months_last_bought_lh_507c37","n_months_last_bought_lh_839f8a","n_months_last_bought_inv_e9f316","n_months_last_bought_grp_caa6ff","n_months_last_bought_grp_fd3bfb",
"n_months_last_bought_lh_e22a6a","n_months_last_bought_grp_70e1dd","n_months_last_bought_grp_e04c3a","n_months_last_bought_grp_fe5fb8","n_months_last_bought_grp_94baec",
"n_months_last_bought_grp_e91421","n_months_last_bought_lh_f852af","n_months_last_bought_lh_947b15","n_months_last_bought_32c74c","recency_giclaim"]
fill_nan_with_0 = ['tot_inforce_pols',"giclaim_amt"]
convert_to_categorical = ["ctrycode_desc"]

In [248]:
for j in convert_to_int:
  df[j] = pd.to_numeric(df[j], errors='coerce', downcast='integer')
for j in convert_to_float:
  try:
    df[j] = pd.to_numeric(df[j], errors='coerce', downcast='float')
  except:
    pass

In [249]:
for j in fill_nan_with_mean:
  df[j].fillna(df[j].mean(), inplace=True)
for j in fill_nan_with_mean_int:
  df[j].fillna(round(df[j].mean()), inplace=True)
for j in fill_nan_with_n1:
  try:
    df[j].fillna(-1, inplace=True) # no key recency_laspe
  except:
    pass
for j in fill_nan_with_0:
  df[j].fillna(0, inplace=True)
for j in fill_nan_with_majority:
  df[j].fillna(df[j].mode()[0], inplace=True)

In [250]:
df.shape

(17992, 255)

In [251]:
# Identify columns starting with 'n_months_last_bought' --> if last bought issurance, likely wont buy one that soon.
target_columns = df.columns[df.columns.str.startswith('n_months_last_bought')]

# Change entries based on the specified condition
df[target_columns] = df[target_columns].applymap(lambda x: 0 if int(x) > 9000 else 1)

# Collate columns and calculate the sum for each row
df['collated_sum'] = df[target_columns].sum(axis=1)

# Assign 1 if the sum is greater than 1, else 0
df['final_result'] = df['collated_sum'].apply(lambda x: 1 if x > 1 else 0)
# Remove the columns that were used in the process
df = df.drop(columns=target_columns)
df.head(100)

C:\Users\tohyizhi\AppData\Local\Temp\ipykernel_28504\1310473115.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['collated_sum'] = df[target_columns].sum(axis=1)
C:\Users\tohyizhi\AppData\Local\Temp\ipykernel_28504\1310473115.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['final_result'] = df['collated_sum'].apply(lambda x: 1 if x > 1 else 0)


ctrycode_desc clttype stat_flag min_occ_date  cltdob_fix  cltsex_fix  \
19550       Singapore       P    ACTIVE   2017-10-31  1974-05-09           1   
4600        Singapore       P    ACTIVE   2007-05-23  1979-11-11           0   
13337       Singapore       P    ACTIVE   2019-08-31  1976-01-28           0   
15074       Singapore       P    ACTIVE   2021-10-18  1976-03-19           1   
19724       Singapore       P    ACTIVE   2018-07-20  1995-07-31           1   
14717       Singapore       P    ACTIVE   2017-07-28  1964-05-02           1   
6307        Singapore       P    ACTIVE   2022-11-06  1996-11-07           1   
4168        Singapore       P    ACTIVE   2018-09-23  1976-09-24           1   
169         Singapore       P    ACTIVE   2013-03-31  1973-03-01           0   
11816       Singapore       P    ACTIVE   2017-09-13  1984-11-06           0   
14245       Singapore       P    ACTIVE   2016-12-01  1986-02-18           1   
4618        Singapore       P    ACTIVE   2018-09-13  1956-11-22           1   
11928       Singapore       G    ACTIVE   2023-01-01  1990-06-21           0   
11195       Singapore       P    ACTIVE   2012-09-30  1972-09-12           0   
6492        Singapore       G    ACTIVE   2023-07-01  1961-01-18           0   
10520       Singapore       P    ACTIVE   2020-12-23  1982-01-28           0   
18743       Singapore       G    ACTIVE   2016-12-01  1982-06-04           1   
15299       Singapore       P    ACTIVE   2010-01-31  1970-01-21           1   
17470       Singapore       P    ACTIVE   2020-01-24  1969-10-22           0   
17726       Singapore       P    ACTIVE   2010-12-01  1962-12-16           0   
5923        Singapore       P    ACTIVE   2013-10-01  1976-11-19           1   
18769       Singapore       P    ACTIVE   2017-02-23  1980-12-26           0   
12938       Singapore       P    ACTIVE   2016-04-30  1976-04-29           0   
3310        Singapore       P    ACTIVE   2010-10-31  1970-10-04           0   
3165        Singapore       P    ACTIVE   2020-03-30  1991-07-19           1   
16323       Singapore       P    ACTIVE   2020-11-24  1982-11-29           1   
12842       Singapore       P    ACTIVE   2015-11-30  1975-11-16           1   
2781        Singapore       P    ACTIVE   2010-12-18  1962-12-19           1   
4417        Singapore       P    ACTIVE   2012-01-25  1957-08-15           0   
7319   Not Applicable       P    ACTIVE   2022-07-01  1965-01-19           0   
4816        Singapore       P    ACTIVE   2016-12-01  1983-07-19           1   
2277        Singapore       P    ACTIVE   2021-01-06  1995-01-15           1   
137         Singapore       P    ACTIVE   2003-11-17  1971-05-13           0   
7014        Singapore       P    ACTIVE   2020-07-16  1981-08-05           1   
3481        Singapore       P    ACTIVE   2011-11-01  1991-08-18           0   
15886       Singapore       P    ACTIVE   2023-05-04  1980-07-05           1   
6848        Singapore       G    ACTIVE   2016-09-01  1990-03-30           1   
4189        Singapore       P    ACTIVE   2008-08-31  1968-08-22           1   
19853       Singapore       P    ACTIVE   2020-09-28  1984-06-29           1   
8332        Singapore       P    ACTIVE   2022-04-21  1980-10-09           0   
9742        Singapore       P    ACTIVE   2003-02-01  1983-07-24           0   
3704        Singapore       G    ACTIVE   2023-01-01  1987-01-19           1   
8029        Singapore       P    ACTIVE   2012-08-13  1989-08-02           1   
12034       Singapore       P    ACTIVE   2010-12-31  1970-12-15           1   
2748        Singapore       P    ACTIVE   2015-03-01  1977-04-25           0   
5391        Singapore       P    ACTIVE   2011-03-23  1969-02-28           0   
4197        Singapore       P    ACTIVE   2018-12-05  1985-07-24           0   
2988        Singapore       P    ACTIVE   2019-03-18  1973-12-23           0   
19557       Singapore       P    ACTIVE   2016-04-25  1966-11-26           0   
17969   

In [252]:
# Identify columns starting with 'lapse_ape'
lapse_ape_columns = [col for col in df.columns if col.startswith('lapse_ape')]

# Select rows where any value in 'lapse_ape' columns is None (NaN)
selected_rows = df[df[lapse_ape_columns].isna().any(axis=1)]

# Display 200 random entries
random_entries = selected_rows.sample(n=min(200, len(selected_rows)), random_state=42)

# Display the result
print("Selected 200 random entries where 'lapse_ape' columns have NaN:")
random_entries.head(200)

Selected 200 random entries where 'lapse_ape' columns have NaN:


ctrycode_desc clttype stat_flag min_occ_date  cltdob_fix  cltsex_fix  \
2097        Singapore       P    ACTIVE   2021-01-11  2002-12-21           0   
5682        Singapore       P    ACTIVE   2007-09-30  1967-09-08           0   
9411        Singapore       G    ACTIVE   2023-01-01  2002-08-29           0   
19776       Singapore       P    ACTIVE   2018-02-05  1989-05-15           0   
15897       Singapore       G    ACTIVE   2016-12-01  1982-01-12           1   
19795       Singapore       P    ACTIVE   2010-12-19  1964-12-20           0   
14543       Singapore       G    ACTIVE   2023-05-17  1987-06-27           1   
11331       Singapore       P    ACTIVE   2023-01-13  1978-02-27           1   
16407       Singapore       G    ACTIVE   2023-01-01  1973-05-06           1   
12255       Singapore       G    ACTIVE   2005-05-01  1981-11-15           0   
18385       Singapore       P    ACTIVE   2017-10-19  1985-05-04           0   
13984       Singapore       P    LAPSED   2020-10-18  1986-12-12           1   
4225        Singapore       G    ACTIVE   2022-11-01  1999-04-05           1   
9290        Singapore       P    ACTIVE   2008-04-01  1989-09-01           0   
4217        Singapore       P    ACTIVE   2012-03-23  1964-05-24           0   
745         Singapore       P    ACTIVE   2008-09-30  1968-09-10           0   
100         Singapore       P    ACTIVE   2018-10-08  1986-02-06           1   
18020       Singapore       P    ACTIVE   2018-12-26  1990-10-09           0   
14824       Singapore       P    ACTIVE   2006-01-01  1974-07-30           0   
11478       Singapore       P    ACTIVE   2023-06-21  1987-03-15           1   
15045       Singapore       G    ACTIVE   2023-01-01  1990-03-21           1   
583         Singapore       P    ACTIVE   2022-09-24  1965-11-03           0   
11531       Singapore       P    ACTIVE   2019-05-02  1972-02-24           0   
16463       Singapore       P    ACTIVE   2021-01-22  1982-02-16           1   
7641        Singapore       P    ACTIVE   2009-01-01  1946-12-06           0   
1299        Singapore       P    ACTIVE   2005-05-19  1986-10-28           0   
5334        Singapore       P    ACTIVE   2016-03-31  1976-03-26           0   
2314        Singapore       P    ACTIVE   2012-07-01  1974-06-02           0   
15093       Singapore       P    ACTIVE   2019-12-31  1981-10-27           0   
10792       Singapore       P    ACTIVE   2016-06-30  1976-06-12           0   
19701       Singapore       P    ACTIVE   2019-10-21  1984-06-21           0   
11661       Singapore       P    ACTIVE   2011-09-08  1975-01-03           1   
16980       Singapore       G    ACTIVE   2023-01-01  1988-07-07           1   
1220        Singapore       P    LAPSED   2020-10-28  1958-01-03           1   
15963       Singapore       P    ACTIVE   2007-04-16  1974-04-03           1   
10586       Singapore       P    ACTIVE   2014-10-31  1974-10-31           1   
17453       Singapore       G    ACTIVE   2016-12-01  1988-03-27           1   
15042       Singapore       G    ACTIVE   2023-06-01  1989-04-22           0   
19957       Singapore       P    ACTIVE   2018-11-07  1985-11-08           1   
3630        Singapore       G    ACTIVE   2023-04-01  1988-05-06           1   
9809        Singapore       P    ACTIVE   2013-05-13  1981-08-06           1   
15162       Singapore       G    ACTIVE   2023-01-01  1970-12-15           0   
9511        Singapore       P    ACTIVE   2013-10-24  1962-10-25           0   
17867       Singapore       G    ACTIVE   2023-04-01  1984-05-11           0   
4253   Not Applicable       P    ACTIVE   2018-05-01  1985-03-02           1   
12513       Singapore       P    ACTIVE   1998-04-01  1968-06-28           0   
16023       Singapore       P    ACTIVE   2008-08-27  1962-10-02           0   
4089        Singapore       P    ACTIVE   2016-11-28  1973-02-12           0   
2596        Singapore       P    ACTIVE   2013-08-21  1977-11-21           0   
8043    

In [253]:
#now, lets see the columns which are in strings
# Get data types for all columns
column_types = df.dtypes

In [254]:
# Identify columns with string (object) data type
string_columns = df.select_dtypes(include='object').columns

# Display information for each column
for col in df.columns:
    unique_values = df[col].nunique()
    unique_values_list = df[col].unique() if unique_values < 6 else None

    print(f"Column: {col} | Data Type: {df[col].dtype} | Unique Values: {unique_values}")

    if unique_values_list is not None:
        print(f"    Unique Values: {unique_values_list}")
        for value in unique_values_list:
            count = df[col].value_counts().get(value, 0)
            percentage = count / len(df) * 100
            print(f"        {value}: {percentage:.2f}% (Count: {count})")
    else:
        print(f"    Unique Values: {unique_values}")

Column: ctrycode_desc | Data Type: object | Unique Values: 26
    Unique Values: 26
Column: clttype | Data Type: object | Unique Values: 3
    Unique Values: ['P' 'G' 'C']
        P: 81.46% (Count: 14657)
        G: 18.40% (Count: 3311)
        C: 0.13% (Count: 24)
Column: stat_flag | Data Type: object | Unique Values: 3
    Unique Values: ['ACTIVE' 'LAPSED' 'MATURED']
        ACTIVE: 95.63% (Count: 17205)
        LAPSED: 4.31% (Count: 775)
        MATURED: 0.07% (Count: 12)
Column: min_occ_date | Data Type: object | Unique Values: 4576
    Unique Values: 4576
Column: cltdob_fix | Data Type: object | Unique Values: 11076
    Unique Values: 11076
Column: cltsex_fix | Data Type: int64 | Unique Values: 2
    Unique Values: [1 0]
        1: 45.61% (Count: 8207)
        0: 54.39% (Count: 9785)
Column: flg_substandard | Data Type: float64 | Unique Values: 2
    Unique Values: [0. 1.]
        0.0: 96.20% (Count: 17308)
        1.0: 3.80% (Count: 684)
Column: flg_is_borderline_standard | Data 

In [255]:
# print which column is type string
pd.set_option('display.max_rows', None)
string_column = df.select_dtypes(exclude=["int64", "float64"]).columns
for i in string_column:
  print(i)


ctrycode_desc
clttype
stat_flag
min_occ_date
cltdob_fix
ape_grp_6fc3e6
ape_grp_de05ae
ape_grp_945b5a
ape_grp_6a5788
ape_ltc_43b9d5
ape_grp_9cdedf
ape_grp_1581d7
ape_grp_22decf
ape_lh_507c37
ape_lh_839f8a
ape_inv_e9f316
ape_grp_caa6ff
ape_grp_fd3bfb
ape_lh_e22a6a
ape_grp_70e1dd
ape_grp_e04c3a
ape_grp_fe5fb8
ape_grp_94baec
ape_grp_e91421
ape_lh_f852af
sumins_grp_6fc3e6
sumins_grp_de05ae
sumins_grp_945b5a
sumins_grp_6a5788
sumins_ltc_43b9d5
sumins_grp_9cdedf
sumins_grp_1581d7
sumins_lh_507c37
sumins_grp_caa6ff
sumins_grp_fd3bfb
sumins_grp_70e1dd
sumins_grp_e91421
sumins_lh_f852af
sumins_lh_947b15
prempaid_grp_6fc3e6
prempaid_ltc_43b9d5
prempaid_lh_839f8a
prempaid_inv_e9f316
prempaid_lh_e22a6a
ape_839f8a
ape_e22a6a
ape_c4bda5
ape_ltc
sumins_839f8a
sumins_ltc
sumins_507c37
prempaid_c4bda5
lapse_ape_grp_6fc3e6
lapse_ape_grp_945b5a
lapse_ape_grp_6a5788
lapse_ape_ltc_43b9d5
lapse_ape_grp_9cdedf
lapse_ape_grp_1581d7
lapse_ape_grp_22decf
lapse_ape_lh_507c37
lapse_ape_lh_839f8a
lapse_ape_grp_caa6

In [256]:
# get the age where user knows about insurance
def calculate_occ_age_days(row):
    try:
        min_occ_date = pd.to_datetime(row['min_occ_date'])
        cltdob_fix = pd.to_datetime(row['cltdob_fix'])
        return (min_occ_date - cltdob_fix).days
    except (TypeError, ValueError):  # Handle TypeError and ValueError exceptions
        return None

df['min_occ_age_days'] = df.apply(calculate_occ_age_days, axis=1)

# Calculate the mean of the column 'col1'
min_occ_age_days_mean = df['min_occ_age_days'].mean()

# Fill NaN values in 'col1' with its mean
df['min_occ_age_days'].fillna(min_occ_age_days_mean, inplace=True)
print(df['min_occ_age_days'].isna().sum())




def calculate_age_days(row):
    try:
        min_occ_date = (pd.to_datetime('2024-01-01'))
        cltdob_fix = pd.to_datetime(row['cltdob_fix'])
        return (min_occ_date - cltdob_fix).days
    except (TypeError, ValueError):
        return None

# df['age_in_days'] = (pd.to_datetime('2024-01-01') - pd.to_datetime(df['cltdob_fix'])).dt.days
df['min_age_days'] = df.apply(calculate_age_days, axis=1)
min_age_days_mean = df['min_age_days'].mean()
df['min_age_days'].fillna(min_age_days_mean, inplace=True)
print(df['min_age_days'].isna().sum())

C:\Users\tohyizhi\AppData\Local\Temp\ipykernel_28504\2281914128.py:10: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['min_occ_age_days'] = df.apply(calculate_occ_age_days, axis=1)


0
0


C:\Users\tohyizhi\AppData\Local\Temp\ipykernel_28504\2281914128.py:31: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['min_age_days'] = df.apply(calculate_age_days, axis=1)


In [257]:
# # understand what data is being dropped
# # Identify object columns
# object_columns = df.select_dtypes(include='object').columns

# # Convert object columns to decimal if needed
# for col in object_columns:
#     try:
#         df[col] = df[col].apply(lambda x: int(x))  # Assuming base-36 conversion for string to decimal
#     except ValueError:
#         # Handle the case where conversion to decimal is not possible
#         print(f"Cannot convert column '{col}' to decimal.")

# # Identify columns to drop based on the number of unique values
# columns_to_drop = [col for col in df.columns if df[col].nunique() > 10]

# # Drop columns with more than 10 unique values
# df_a = df.drop(columns=columns_to_drop)

# # Convert the remaining object columns to one-hot encoding
# df_a = pd.get_dummies(df_a, columns=[col for col in df_a.columns if col not in columns_to_drop])
# df = df_a


In [258]:
df.shape

(17992, 230)

In [259]:
# check if there is any na from other rows
from IPython.display import display
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
print(df.isna().sum())

ctrycode_desc                            0
clttype                                  0
stat_flag                                0
min_occ_date                             0
cltdob_fix                               0
cltsex_fix                               0
flg_substandard                          0
flg_is_borderline_standard               0
flg_is_revised_term                      0
flg_is_rental_flat                       0
flg_has_health_claim                     0
flg_has_life_claim                       0
flg_gi_claim                             0
flg_is_proposal                          0
flg_with_preauthorisation                0
flg_is_returned_mail                     0
is_consent_to_mail                       0
is_consent_to_email                      0
is_consent_to_call                       0
is_consent_to_sms                        0
is_valid_dm                              0
is_valid_email                           0
is_housewife_retiree                     0
is_sg_pr   

In [260]:
# basic processing of data

# Convert target col to 0 or 1
df["f_purchase_lh"] = df["f_purchase_lh"].fillna(0)

# Identifiy numeric columns and fill null values with the median value
numeric_cols = df.select_dtypes(include=["int64", "float64"]).columns
df[numeric_cols] = df[numeric_cols].apply(lambda x: x.fillna(x.median()))

# Drop non-numeric cols
non_numeric_cols = df.select_dtypes(include=["string", "object"]).columns
df = df.drop(columns=non_numeric_cols)
df.dropna(axis=1, inplace=True)
df.shape


(17992, 223)

In [261]:



# Split the dataset.
# Separate features and labels
X = df.drop("f_purchase_lh", axis=1)
y = df["f_purchase_lh"]

# Split the data into training and testing sets with stratification
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, stratify=y, random_state=42)

# Display the shapes of the resulting sets
print("Training set shape:")
print(X_train.shape, y_train.shape)
print("\nTesting set shape:")
print(X_test.shape, y_test.shape)
# balance the datset

from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
# Define the resampling strategy
# resampling_strategy = {0: int(len(y_train[y_train == 0]) * 0.5), 1: len(y_train[y_train == 1]) * 1.5}
resampling_strategy = {0: int(len(y_train[y_train == 0]) * 0.5)}

# Apply RandomUnderSampler to downsample the majority class
rus = RandomUnderSampler(sampling_strategy=resampling_strategy, random_state=42)
X_resampled, y_resampled = rus.fit_resample(X_train, y_train)

# Apply SMOTE to upsample the minority class
smote = SMOTE(sampling_strategy='auto', k_neighbors=5, random_state=42)
X_resampled, y_resampled = smote.fit_resample(X_resampled, y_resampled)





Training set shape:
(14393, 222) (14393,)

Testing set shape:
(3599, 222) (3599,)


In [262]:
# # choose a few features for random forest # To be confirmed
# basic_columns = ["race_desc","ctrycode_desc","clttype","stat_flag","cltsex_fix","flg_substandard","flg_is_borderline_standard","flg_is_revised_term	flg_is_rental_flat","flg_has_health_claim","flg_has_life_claim","flg_gi_claim","flg_is_proposal","flg_with_preauthorisation","flg_is_returned_mail","is_consent_to_mail","is_consent_to_email","is_consent_to_call","is_consent_to_sms","is_valid_dm","is_valid_email","is_housewife_retiree","is_sg_pr","is_class_1_2","is_dependent_in_at_least_1_policy","f_ever_declined_la","hh_20","pop_20","hh_size","hh_size_est","annual_income_est","n_months_last_bought_products","flg_latest_being_lapse","flg_latest_being_cancel","recency_laps","recency_cancel","tot_inforce_pols","tot_cancel_pols"]
import pandas as pd
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectFromModel

# Assume 'X_resampled' and 'y_resampled' are your balanced training set
# For demonstration purposes, let's create a sample DataFrame
# data = {'Feature1': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10],
#         'Feature2': [0, 1, 1, 1, 0, 1, 0, 0, 1, 1],
#         'Label': [0, 1, 0, 1, 0, 1, 0, 0, 1, 1]}
# df = pd.DataFrame(data)

# Separate features and labels
# y = df["f_purchase_lh"]
# X = df.drop(columns=['f_purchase_lh'])
X,y = X_resampled, y_resampled
X,y = X_train, y_train


# Train a Random Forest model
rf_model = RandomForestClassifier(random_state=42)
rf_model.fit(X, y)
# rf_model.fit(X_resampled, y_resampled)

# Get feature importances from the model
feature_importances = rf_model.feature_importances_

# Create a DataFrame to display feature importances
feature_importance_df = pd.DataFrame({'Feature': X_resampled.columns, 'Importance': feature_importances})
feature_importance_df = feature_importance_df.sort_values(by='Importance', ascending=False)

# Display the ranked feature importances
print("Ranked Feature Importances:")
print(feature_importance_df)



Ranked Feature Importances:
                               Feature    Importance
221                       min_age_days  4.402517e-02
220                   min_occ_age_days  4.205949e-02
23                              pop_20  3.961445e-02
24                             hh_size  3.809065e-02
22                               hh_20  3.570025e-02
29                       recency_lapse  3.499629e-02
187                           f_retail  2.138965e-02
192        n_months_since_visit_affcon  2.073914e-02
194                     recency_clmcon  1.978966e-02
31                    tot_inforce_pols  1.731789e-02
26                   annual_income_est  1.627036e-02
218                       collated_sum  1.538509e-02
25                         hh_size_est  1.524977e-02
95                          ape_507c37  1.416041e-02
109                    prempaid_507c37  1.388454e-02
213                  f_ever_bought_sum  1.301806e-02
163                   f_ever_bought_gi  1.230512e-02
104               

In [263]:
# Select the top 10 features
selected_features = feature_importance_df.head(10)['Feature'].tolist()

# Create a new training set with only the selected features
X_train = X_train[selected_features]
X_test = X_test[selected_features]

# Display the selected features
print("Selected Features:")
print(selected_features)

# Display the shape of the new training set
print("\nNew Training Set Shape:")
print(X_train.shape)


Selected Features:
['min_age_days', 'min_occ_age_days', 'pop_20', 'hh_size', 'hh_20', 'recency_lapse', 'f_retail', 'n_months_since_visit_affcon', 'recency_clmcon', 'tot_inforce_pols']

New Training Set Shape:
(14393, 10)


In [264]:
#use random forest classifier to see the importance of the features
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.ensemble import RandomForestClassifier
rf = RandomForestClassifier(n_estimators=1000)
kf = KFold(n_splits=10)
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []
for train_index, test_index in kf.split(X):
  XX_train = X.iloc[train_index]
  YY_train = y.iloc[train_index]

  XX_test = X.iloc[test_index]
  YY_test = y.iloc[test_index]

  rf.fit(XX_train,YY_train)
  YY_pred = rf.predict(XX_test)
  accuracy_scores.append(accuracy_score(YY_test, YY_pred))
  precision_scores.append(precision_score(YY_test, YY_pred))
  recall_scores.append(recall_score(YY_test, YY_pred))
  f1_scores.append(f1_score(YY_test, YY_pred))
  break

feature_importance_scores = rf.feature_importances_
# Create a DataFrame to display feature importance
print(len(X.columns))
print(len(feature_importance_scores))
feature_importance_df = pd.DataFrame({'Feature': X.columns, 'Importance': feature_importance_scores})

# Sort features by importance (descending order)
feature_importance_df = feature_importance_df.sort_values(by='Importance', ascending=False)

print("Feature Importance:")
print(feature_importance_df)


# Calculate average scores
avg_accuracy = sum(accuracy_scores) / len(accuracy_scores)
avg_precision = sum(precision_scores) / len(precision_scores)
avg_recall = sum(recall_scores) / len(recall_scores)
avg_f1 = sum(f1_scores) / len(f1_scores)

print("Average Accuracy:", avg_accuracy)
print("Average Precision:", avg_precision)
print("Average Recall:", avg_recall)
print("Average F1 Score:", avg_f1)

222
222
Feature Importance:
                               Feature    Importance
220                   min_occ_age_days  4.360524e-02
221                       min_age_days  4.289563e-02
24                             hh_size  3.764596e-02
23                              pop_20  3.750675e-02
29                       recency_lapse  3.601931e-02
22                               hh_20  3.426850e-02
192        n_months_since_visit_affcon  2.036559e-02
187                           f_retail  1.959356e-02
194                     recency_clmcon  1.902802e-02
31                    tot_inforce_pols  1.756413e-02
26                   annual_income_est  1.658088e-02
218                       collated_sum  1.604198e-02
25                         hh_size_est  1.564428e-02
109                    prempaid_507c37  1.487024e-02
95                          ape_507c37  1.481983e-02
213                  f_ever_bought_sum  1.366727e-02
104                      sumins_507c37  1.330851e-02
163               

In [265]:
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.ensemble import RandomForestClassifier
# kfold on random forest
kf = KFold(n_splits=10)
rf = RandomForestClassifier()
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []
for train_index, test_index in kf.split(X_train):
  XX_train = X_train.iloc[train_index]
  YY_train = y_train.iloc[train_index]

  XX_test = X_train.iloc[test_index]
  YY_test = y_train.iloc[test_index]

  rf.fit(XX_train,YY_train)
  YY_pred = rf.predict(XX_test)
  accuracy_scores.append(accuracy_score(YY_test, YY_pred))
  precision_scores.append(precision_score(YY_test, YY_pred))
  recall_scores.append(recall_score(YY_test, YY_pred))
  f1_scores.append(f1_score(YY_test, YY_pred))


# Calculate average scores
avg_accuracy = sum(accuracy_scores) / len(accuracy_scores)
avg_precision = sum(precision_scores) / len(precision_scores)
avg_recall = sum(recall_scores) / len(recall_scores)
avg_f1 = sum(f1_scores) / len(f1_scores)

print("Average Accuracy:", avg_accuracy)
print("Average Precision:", avg_precision)
print("Average Recall:", avg_recall)
print("Average F1 Score:", avg_f1)





c:\Users\tohyizhi\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\tohyizhi\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\tohyizhi\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\tohyizhi\A

Average Accuracy: 0.9598422901706434
Average Precision: 0.125
Average Recall: 0.004105090311986864
Average F1 Score: 0.0077376565954310975


c:\Users\tohyizhi\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [266]:
import pandas as pd
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
from sklearn.ensemble import RandomForestClassifier
from imblearn.pipeline import Pipeline

# Assuming X, y are your features and labels
# Replace this with your actual data
NUM_TOP_FEATURES = 25
X, y = df[feature_importance_df['Feature'][:NUM_TOP_FEATURES]], df['f_purchase_lh']

# Specify the number of folds for cross-validation
n_splits = 5  # You can adjust this based on your preference

# Initialize StratifiedKFold
stratified_kfold = StratifiedKFold(n_splits=n_splits, shuffle=True, random_state=42)

# Initialize your classifier
classifier = RandomForestClassifier(random_state=42)

# Initialize variables to store results
accuracy_scores = []
precision_scores = []
recall_scores = []
f1_scores = []

# Perform cross-validation
for train_index, val_index in stratified_kfold.split(X, y):
    X_train, X_val = X.iloc[train_index], X.iloc[val_index]
    y_train, y_val = y.iloc[train_index], y.iloc[val_index]

    # Create a pipeline with RandomUnderSampler and SMOTE for training set
    resampling_pipeline = Pipeline([
        ('under', RandomUnderSampler(sampling_strategy='majority', random_state=42)),
        ('over', SMOTE(sampling_strategy='auto', k_neighbors=5, random_state=42))
    ])

    X_train_resampled, y_train_resampled = resampling_pipeline.fit_resample(X_train, y_train)

    # Train the classifier on the resampled training set
    classifier.fit(X_train_resampled, y_train_resampled)

    # Evaluate the classifier on the validation set
    y_pred_val = classifier.predict(X_val)

    # Calculate metrics for the validation set
    accuracy_scores.append(accuracy_score(y_val, y_pred_val))
    precision_scores.append(precision_score(y_val, y_pred_val))
    recall_scores.append(recall_score(y_val, y_pred_val))
    f1_scores.append(f1_score(y_val, y_pred_val))

# Calculate average metrics across all folds
avg_accuracy = sum(accuracy_scores) / n_splits
avg_precision = sum(precision_scores) / n_splits
avg_recall = sum(recall_scores) / n_splits
avg_f1 = sum(f1_scores) / n_splits

# Display the average metrics
print("Average Accuracy:", avg_accuracy)
print("Average Precision:", avg_precision)
print("Average Recall:", avg_recall)
print("Average F1 Score:", avg_f1)
print()


Average Accuracy: 0.7146511730993153
Average Precision: 0.09728033792633349
Average Recall: 0.752112676056338
Average F1 Score: 0.17224319226971868



In [267]:
from sklearn.tree import DecisionTreeClassifier
import pandas as pd
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
from sklearn.ensemble import RandomForestClassifier
from imblearn.pipeline import Pipeline

def run_decision_tree_k_fold(X, y, k):
    # Specify the number of folds for cross-validation
    n_splits = k

    # Initialize StratifiedKFold
    stratified_kfold = StratifiedKFold(n_splits=n_splits, shuffle=True, random_state=42)

    # Initialize your classifier
    classifier = DecisionTreeClassifier(random_state=42)

    # Initialize variables to store results
    accuracy_scores = []
    precision_scores = []
    recall_scores = []
    f1_scores = []

    # Perform cross-validation
    for train_index, val_index in stratified_kfold.split(X, y):
        X_train, X_val = X.iloc[train_index], X.iloc[val_index]
        y_train, y_val = y.iloc[train_index], y.iloc[val_index]

        # Create a pipeline with RandomUnderSampler and SMOTE for training set
        resampling_pipeline = Pipeline([
            ('under', RandomUnderSampler(sampling_strategy='majority', random_state=42)),
            ('over', SMOTE(sampling_strategy='auto', k_neighbors=5, random_state=42))
        ])

        X_train_resampled, y_train_resampled = resampling_pipeline.fit_resample(X_train, y_train)

        # Train the classifier on the resampled training set
        classifier.fit(X_train_resampled, y_train_resampled)

        # Evaluate the classifier on the validation set
        y_pred_val = classifier.predict(X_val)

        # Calculate metrics for the validation set
        accuracy_scores.append(accuracy_score(y_val, y_pred_val))
        precision_scores.append(precision_score(y_val, y_pred_val))
        recall_scores.append(recall_score(y_val, y_pred_val))
        f1_scores.append(f1_score(y_val, y_pred_val))

    # Calculate average metrics across all folds
    avg_accuracy = sum(accuracy_scores) / n_splits
    avg_precision = sum(precision_scores) / n_splits
    avg_recall = sum(recall_scores) / n_splits
    avg_f1 = sum(f1_scores) / n_splits

    # Display the average metrics
    print("Decision Tree Classifier Metrics:")
    print("Average Accuracy:", avg_accuracy)
    print("Average Precision:", avg_precision)
    print("Average Recall:", avg_recall)
    print("Average F1 Score:", avg_f1)
    print()
    return ((avg_f1, avg_precision, avg_recall, avg_precision),X.columns.tolist())


In [268]:
# import itertools
# # Now, let's run decision trees on all combinations of predictor columns
# feature_columns = list(feature_importance_df['Feature'][:])

# all_feature_combinations = []
# results = []

# # for r in range(5, len(feature_columns) + 1):
# for r in range(2, 4):
#     combinations = list(itertools.combinations(feature_columns, r))
#     all_feature_combinations.extend([list(combination) for combination in combinations])

# # Assuming you have a function run_decision_tree_k_fold, you can call it like this:
# for features in all_feature_combinations:
#     print("Running decision tree for features:", features)
#     # run_decision_tree_k_fold(X[features], y['f_purchase_lh'], 10)
#     try:
#       result = run_decision_tree_k_fold(X[features], y, 5)
#     except:
#       continue
#     results.append(result)


In [269]:
#top 10 features
columns = []
columns.append('f_retail')
columns.append('f_ever_bought_gi')
columns.append('is_valid_sum')
columns.append('n_months_since_visit_affcon')
columns.append('f_ever_bought_gi')
columns.append('recency_clmcon')
columns.append('annual_income_est')
columns.append('hh_size_est')
columns.append('recency_lapse')
columns.append('is_consent_sum')
# columns.append('hh_size_est')
print(columns)

['f_retail', 'f_ever_bought_gi', 'is_valid_sum', 'n_months_since_visit_affcon', 'f_ever_bought_gi', 'recency_clmcon', 'annual_income_est', 'hh_size_est', 'recency_lapse', 'is_consent_sum']


In [270]:
# import itertools
# # Now, let's run decision trees on all combinations of predictor columns
# # feature_columns = list(feature_importance_df['Feature'][:NUM_TOP_FEATURES])

# all_feature_combinations = []
# results1 = []

# # for r in range(5, len(feature_columns) + 1):
# for r in range(2, 9):
#     # combinations = list(itertools.combinations(feature_columns, r))
#     combinations = list(itertools.combinations(columns, r))
#     all_feature_combinations.extend([list(combination) for combination in combinations])

# # Assuming you have a function run_decision_tree_k_fold, you can call it like this:
# for features in all_feature_combinations:
#     print("Running decision tree for features:", features)
#     # run_decision_tree_k_fold(X[features], y['f_purchase_lh'], 10)
#     result = run_decision_tree_k_fold(X[features], y, 5)
#     results1.append(result)


In [271]:
# # results.sort(reverse = True)
# sorted_data_desc = sorted(results, key=lambda x: x[0], reverse=True)
# for i in range(30):
#   print(f'{i+1}:{sorted_data_desc[i][0]} {sorted_data_desc[i][1]}')

In [272]:
from sklearn.ensemble import RandomForestClassifier
unique_column_names = ['f_retail', 'f_ever_bought_gi', 'is_valid_sum']
X_train_updated = X_train[unique_column_names]
# Train your model
model = RandomForestClassifier()
model.fit(X_train, y_train)

# Get feature importances
feature_importances = model.feature_importances_

In [273]:
y = df["f_purchase_lh"]
X = df.drop(columns=['f_purchase_lh'])
X = df[['f_retail', 'f_ever_bought_gi', 'is_valid_sum']]

In [274]:
# from sklearn.model_selection import GridSearchCV, cross_val_score, StratifiedKFold
# from sklearn.preprocessing import StandardScaler
# from sklearn.linear_model import LogisticRegression
# from sklearn.tree import DecisionTreeClassifier
# from sklearn.svm import SVC
# from sklearn.neural_network import MLPClassifier
# from xgboost import XGBClassifier
# from sklearn.metrics import accuracy_score, classification_report

# # Assume X_train and y_train are your feature and target variables

# # Step 1: Split the data into training and testing sets
# X_train, X_test, y_train, y_test = train_test_split(X_train, y_train, test_size=0.2, random_state=42)

# from imblearn.over_sampling import RandomOverSampler
# from imblearn.under_sampling import RandomUnderSampler
# # Define the resampling strategy
# # resampling_strategy = {0: int(len(y_train[y_train == 0]) * 0.5), 1: len(y_train[y_train == 1]) * 1.5}
# resampling_strategy = {1: len(y_train[y_train == 1]) * 3}
# # resampling_strategy = {0: int(len(y_train[y_train == 0]) * 0.5)}

# # Apply RandomUnderSampler to downsample the majority class
# # rus = RandomUnderSampler(sampling_strategy=resampling_strategy, random_state=42)
# # X_resampled, y_resampled = rus.fit_resample(X_train, y_train)
# rus = RandomOverSampler(sampling_strategy=resampling_strategy, random_state=42)
# X_resampled, y_resampled = rus.fit_resample(X_train, y_train)

# X_train, y_train = X_resampled, y_resampled
# # Step 2: Preprocess the data (You might need to handle missing values, categorical variables, etc.)
# # For simplicity, let's just use StandardScaler for numeric features
# scaler = StandardScaler()
# X_train_scaled = scaler.fit_transform(X_train)
# X_test_scaled = scaler.transform(X_test)

# import pickle

# with open('scaler.pickle', 'wb') as file:
#     # Serialize and write the variable to the file
#     pickle.dump(scaler, file)

# # Step 3: Define models and their respective parameter grids
# models = {
#     'Logistic Regression': (LogisticRegression(), {'C': [0.001, 0.01, 0.1, 1, 10, 100]}),
#     'Decision Tree': (DecisionTreeClassifier(), {'max_depth': [3, 5, 7, 10]}),
#     'Support Vector Classifier': (SVC(), {'C': [0.1, 1, 10], 'gamma': [0.1, 0.01, 0.001], 'kernel': ['linear', 'rbf', 'poly']}),
#     'Neural Network': (MLPClassifier(), {'hidden_layer_sizes': [(50,), (100,), (50, 50)], 'alpha': [0.0001, 0.001, 0.01]}),
#     'XGBoost': (XGBClassifier(), {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.1, 0.2],
#                                    'max_depth': [3, 5, 7], 'subsample': [0.8, 1.0], 'colsample_bytree': [0.8, 1.0]})
# }

# # Step 4: Train and evaluate each model with GridSearchCV
# for model_name, (model, param_grid) in models.items():
#     print(f"Training {model_name}...")

#     # Use StratifiedKFold for classification tasks
#     kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

#     # Grid search
#     grid_search = GridSearchCV(model, param_grid=param_grid, scoring='f1', cv=kfold,verbose=2)
#     grid_search.fit(X_train_scaled, y_train)

#     # Best parameters and their corresponding accuracy
#     best_params = grid_search.best_params_
#     best_accuracy = grid_search.best_score_

#     print(f"Best Parameters for {model_name}:")
#     print(best_params)
#     print(f"Best Accuracy: {best_accuracy:.4f}")

#     # Train the model with the best parameters
#     best_model = model.set_params(**best_params)
#     best_model.fit(X_train_scaled, y_train)

#     # Evaluate the model on the test set
#     y_pred = best_model.predict(X_test_scaled)

#     accuracy = accuracy_score(y_test, y_pred)
#     report = classification_report(y_test, y_pred)

#     print(f"Test Accuracy for {model_name}: {accuracy:.4f}")
#     print("Classification Report:")
#     print(report)
#     print("")

# # Note: Adjust the parameter grids and models according to your specific requirements.


In [275]:
# from sklearn.model_selection import GridSearchCV, cross_val_score, StratifiedKFold
# from sklearn.preprocessing import StandardScaler
# from sklearn.linear_model import LogisticRegression
# from sklearn.tree import DecisionTreeClassifier
# from sklearn.svm import SVC
# from sklearn.neural_network import MLPClassifier
# from xgboost import XGBClassifier
# from sklearn.metrics import accuracy_score, classification_report

# # Assume X_train and y_train are your feature and target variables

# # Step 1: Split the data into training and testing sets
# X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# from imblearn.over_sampling import RandomOverSampler
# from imblearn.under_sampling import RandomUnderSampler
# # Define the resampling strategy
# # resampling_strategy = {0: int(len(y_train[y_train == 0]) * 0.5), 1: len(y_train[y_train == 1]) * 1.5}
# resampling_strategy = {1: len(y_train[y_train == 1]) * 3}
# # resampling_strategy = {0: int(len(y_train[y_train == 0]) * 0.5)}

# # Apply RandomUnderSampler to downsample the majority class
# # rus = RandomUnderSampler(sampling_strategy=resampling_strategy, random_state=42)
# # X_resampled, y_resampled = rus.fit_resample(X_train, y_train)
# rus = RandomOverSampler(sampling_strategy=resampling_strategy, random_state=42)
# X_resampled, y_resampled = rus.fit_resample(X_train, y_train)

# X_train, y_train = X_resampled, y_resampled
# # Step 2: Preprocess the data (You might need to handle missing values, categorical variables, etc.)
# # For simplicity, let's just use StandardScaler for numeric features
# scaler = StandardScaler()
# X_train_scaled = scaler.fit_transform(X_train)
# X_test_scaled = scaler.transform(X_test)

# import pickle

# with open('scaler.pickle', 'wb') as file:
#     # Serialize and write the variable to the file
#     pickle.dump(scaler, file)

# # Step 3: Define models and their respective parameter grids
# models = {
#     'Logistic Regression': (LogisticRegression(), {'C': [0.001, 0.01, 0.1, 1, 10, 100]}),
#     'Decision Tree': (DecisionTreeClassifier(), {'max_depth': [3, 5, 7, 10]}),
#     'Support Vector Classifier': (SVC(), {'C': [0.1, 1, 10], 'gamma': [0.1, 0.01, 0.001], 'kernel': ['linear', 'rbf', 'poly']}),
#     'Neural Network': (MLPClassifier(), {'hidden_layer_sizes': [(50,), (100,), (50, 50)], 'alpha': [0.0001, 0.001, 0.01]}),
#     'XGBoost': (XGBClassifier(), {'n_estimators': [50, 100, 200], 'learning_rate': [0.01, 0.1, 0.2],
#                                    'max_depth': [3, 5, 7], 'subsample': [0.8, 1.0], 'colsample_bytree': [0.8, 1.0]}),
#     'Random Forest': (RandomForestClassifier(), {'n_estimators': [50, 100, 200], 'max_depth': [3, 5, 7, 10]})
# }

# # Step 4: Train and evaluate each model with GridSearchCV
# for model_name, (model, param_grid) in models.items():
#     print(f"Training {model_name}...")

#     # Use StratifiedKFold for classification tasks
#     kfold = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

#     # Grid search
#     grid_search = GridSearchCV(model, param_grid=param_grid, scoring='f1', cv=kfold,verbose=2)
#     grid_search.fit(X_train_scaled, y_train)

#     # Best parameters and their corresponding accuracy
#     best_params = grid_search.best_params_
#     best_accuracy = grid_search.best_score_

#     print(f"Best Parameters for {model_name}:")
#     print(best_params)
#     print(f"Best Accuracy: {best_accuracy:.4f}")

#     # Train the model with the best parameters
#     best_model = model.set_params(**best_params)
#     best_model.fit(X_train_scaled, y_train)

#     # Evaluate the model on the test set
#     y_pred = best_model.predict(X_test_scaled)

#     accuracy = accuracy_score(y_test, y_pred)
#     report = classification_report(y_test, y_pred)

#     print(f"Test Accuracy for {model_name}: {accuracy:.4f}")
#     print("Classification Report:")
#     print(report)
#     print("")

# # Note: Adjust the parameter grids and models according to your specific requirements.


In [276]:
# Best parameter
from sklearn.linear_model import LogisticRegression
from imblearn.over_sampling import RandomOverSampler
from imblearn.under_sampling import RandomUnderSampler

resampling_strategy = {1: len(y_train[y_train == 1]) * 3}
# resampling_strategy = {0: int(len(y_train[y_train == 0]) * 0.5)}

# Apply RandomUnderSampler to downsample the majority class
# rus = RandomUnderSampler(sampling_strategy=resampling_strategy, random_state=42)
# X_resampled, y_resampled = rus.fit_resample(X, y)
rus = RandomOverSampler(sampling_strategy=resampling_strategy, random_state=42)
X_resampled, y_resampled = rus.fit_resample(X, y)
lr = LogisticRegression(C=10)
lr.fit(X,y)
import pickle
with open('lr.pickle', 'wb') as file:
    # Serialize and write the variable to the file
    pickle.dump(lr, file)


In [277]:
# Can have as many cells as you want for code
# we require train data to configure standscaler
import pandas as pd
filepath = "./data/catB_train.parquet"
# the initialised filepath MUST be a relative path to a folder named data that contains the parquet file

In [278]:
# best model
def testing_hidden_data(hidden_data: pd.DataFrame) -> list:
  '''DO NOT REMOVE THIS FUNCTION.
  The function accepts a dataframe as input and return an iterable (list)
  of binary classes as output.

  The function should be coded to test on hidden data
  and should include any preprocessing functions needed for your model to perform.

  All relevant code MUST be included in this function.'''
  # import statements
  from sklearn.linear_model import LogisticRegression
  import pickle
  
  is_valid_columns = [col for col in hidden_data.columns if col.startswith('is_valid')]

  # Create new columns 'is_consent_sum' and 'is_valid_sum' containing the sums

  hidden_data['is_valid_sum'] = hidden_data[is_valid_columns].sum(axis=1)


  # using the training data, configure standard scaler
  X = hidden_data[['f_retail', 'f_ever_bought_gi', 'is_valid_sum']]
  print(X.shape)
  # get the necessary columns in
  scaler = None
  lr = None
  with open("scaler.pickle", 'rb') as file:
    # Deserialize and retrieve the variable from the file
    scaler = pickle.load(file)
  X_scaled = scaler.transform(X)
  with open("lr.pickle", 'rb') as file:
    # Deserialize and retrieve the variable from the file
    lr = pickle.load(file)
  result = lr.predict(X_scaled)
  return result

In [279]:
# This cell should output a list of predictions.
test_df = pd.read_parquet(filepath)
test_df = test_df.drop(columns=["f_purchase_lh"])
print(testing_hidden_data(test_df))

(17992, 3)
[0. 0. 0. ... 0. 1. 0.]


c:\Users\tohyizhi\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\base.py:439: UserWarning: X does not have valid feature names, but LogisticRegression was fitted with feature names
  warnings.warn(
